In [1]:
import os
os.chdir('..')

In [2]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [3]:
ll examples/

total 8
-rw-rw-r-- 1 henrik    0 Sep 30 20:40 __init__.py
drwxrwxr-x 2 henrik 4096 Sep 30 20:40 __pycache__/
drwxrwxr-x 3 henrik 4096 Sep 30 20:30 three_tank_system/


In [4]:
from examples.three_tank_system.dataset import ThreeTankBaseDataSet
from torch.utils.data import DataLoader

In [5]:
dataset = ThreeTankBaseDataSet(debug=True)

In [6]:
batch_size = 2000
dataloader = DataLoader(dataset, batch_size=batch_size, num_workers=24)

In [7]:
from sindy_autoencoder_cps.lightning_module import SINDyAutoencoder
import yaml
# MODEL_VERSION = 'freq_and_phase'
MODEL_VERSION = 'version_54'

hparams_path = f'./lightning_logs/{MODEL_VERSION}/hparams.yaml'
with open(hparams_path, 'r') as stream:
        hparam_dct = yaml.safe_load(stream)
ckpt_file_name = os.listdir(f'./lightning_logs/{MODEL_VERSION}/checkpoints/')[-1]
ckpt_file_path = f'./lightning_logs/{MODEL_VERSION}/checkpoints/{ckpt_file_name}'
model = SINDyAutoencoder.load_from_checkpoint(ckpt_file_path)
model

Global seed set to 12354


SINDyAutoencoder(
  (activation_function): Tanh()
  (phi_x): Encoder(
    (fc1): Linear(in_features=3, out_features=1028, bias=True)
    (fc2): Linear(in_features=1028, out_features=512, bias=True)
    (fc3): Linear(in_features=512, out_features=128, bias=True)
    (fc4): Linear(in_features=128, out_features=64, bias=True)
    (fc5): Linear(in_features=64, out_features=3, bias=True)
    (activation): Tanh()
  )
  (psi_z): Decoder(
    (fc1): Linear(in_features=3, out_features=64, bias=True)
    (fc2): Linear(in_features=64, out_features=128, bias=True)
    (fc3): Linear(in_features=128, out_features=512, bias=True)
    (fc4): Linear(in_features=512, out_features=1028, bias=True)
    (fc5): Linear(in_features=1028, out_features=3, bias=True)
    (activation): Tanh()
  )
)

In [8]:
model.SINDyLibrary.device

'cuda:0'

In [9]:
batches = iter(dataloader)

In [10]:
x, xdot, idxs = batches.next()
print(f'shape x: {x.shape},   shape xdot: {xdot.shape}')

shape x: torch.Size([2000, 3]),   shape xdot: torch.Size([2000, 3])


In [11]:
x_hat, xdot_hat, z, zdot, zdot_hat = model.cuda()(x.cuda(), xdot.cuda())

In [12]:
#select random sample and compare original and recostruction
sample = 0
# sample = 477
x_sample = x[sample, :].cpu().detach().numpy()
xhat_sample = x_hat[sample, :].cpu().detach().numpy()
z_sample = z[sample, :].cpu().detach().numpy()
xdot_sample = xdot[sample, :].cpu().detach().numpy()
xdot_hat_sample = xdot_hat[sample, :].cpu().detach().numpy()
zdot_sample = zdot[sample, :].cpu().detach().numpy()
zdot_hat_sample = zdot_hat[sample, :].cpu().detach().numpy()
idx_sample = idxs[sample]

In [13]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np

fig = make_subplots(rows=3, cols=3, shared_xaxes=False)

for i in range(3):
    fig.add_trace(go.Scatter(x=x[:, i].cpu().detach().numpy(),
                       y=x_hat[:, i].cpu().detach().numpy(),
                      mode='markers', name=f'x_hat{i} over x{i}',
#                              marker_color='blue',
                             opacity=.7), row=1, col=1+i)
    fig.add_trace(go.Scatter(x=xdot[:, i].cpu().detach().numpy(),
                       y=xdot_hat[:, i].cpu().detach().numpy(),
                      mode='markers', name=f'z_hat{i} over z{i}',
#                              marker_color='blue',
                             opacity=.7), row=2, col=1+i)
    fig.add_trace(go.Scatter(x=zdot[:, i].cpu().detach().numpy(),
                       y=zdot_hat[:, i].cpu().detach().numpy(),
                      mode='markers', name=f'zdot_hat{i} over zdot{i}',
#                              marker_color='blue',
                             opacity=.7), row=3, col=1+i)
fig.show()

In [14]:
x_sample

array([0.6460232 , 0.27307063, 0.17744896], dtype=float32)

In [15]:
xhat_sample

array([0.6314125 , 0.28705597, 0.16245484], dtype=float32)

In [16]:
z_sample

array([-0.37413275, -1.001703  , -0.11948831], dtype=float32)

In [17]:
zdot_sample

array([-0.00354156,  0.00682851,  0.00246725], dtype=float32)

In [18]:
xdot_sample

array([-0.02697735,  0.01328168,  0.01369567], dtype=float32)

In [19]:
xdot_hat_sample

array([-0.03256923,  0.01676306,  0.01645107], dtype=float32)

In [20]:
zdot_hat_sample

array([-0.00409074,  0.00926065,  0.00439139], dtype=float32)

In [21]:
import pandas as pd
XI = model.XI.cpu().detach().numpy()
XI.max()
df_XI = pd.DataFrame(XI, columns=['z0_dot_hat', 'z1_dot_hat', 'z2_dot_hat'])
df_XI.index=model.SINDyLibrary.feature_names

In [22]:
import plotly.express as px
print(model.SINDyLibrary.feature_names)
px.imshow(df_XI.abs())

['1', 'z0', 'z1', 'z2', 'z0*z1', 'z0*z2', 'z1*z2', 'z0*z0*z0', 'z0*z0*z1', 'z0*z0*z2', 'z0*z1*z1', 'z0*z1*z2', 'z0*z2*z2', 'z1*z1*z1', 'z1*z1*z2', 'z1*z2*z2', 'z2*z2*z2', 'sign(z0-z1)*sqrt(|z0-z1|)', 'sign(z0-z2)*sqrt(|z0-z2|)', 'sign(z1-z2)*sqrt(|z1-z2|)']


In [23]:
import plotly.express as px
print(model.SINDyLibrary.feature_names)
px.imshow(df_XI.abs())

['1', 'z0', 'z1', 'z2', 'z0*z1', 'z0*z2', 'z1*z2', 'z0*z0*z0', 'z0*z0*z1', 'z0*z0*z2', 'z0*z1*z1', 'z0*z1*z2', 'z0*z2*z2', 'z1*z1*z1', 'z1*z1*z2', 'z1*z2*z2', 'z2*z2*z2', 'sign(z0-z1)*sqrt(|z0-z1|)', 'sign(z0-z2)*sqrt(|z0-z2|)', 'sign(z1-z2)*sqrt(|z1-z2|)']


In [24]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np

fig = make_subplots(rows=2, cols=3, shared_xaxes=True)

for i in range(3):
    fig.add_trace(go.Scatter(x=np.array(range(z.shape[0])),
                       y=z[:, i].cpu().detach().numpy(),
                      mode='markers', name=f'z{i}',
                             marker_color='blue', opacity=.5), row=1, col=1+i,
                    )
for i in range(3):
    fig.add_trace(go.Scatter(x=np.array(range(z.shape[0])),
                       y=zdot_hat[:, i].cpu().detach().numpy(),
                      mode='markers', name=f'zdot_hat{i}',
                            marker_color='blue', opacity=.4), row=2, col=1+i)
for i in range(3):
    fig.add_trace(go.Scatter(x=np.array(range(z.shape[0])),
                       y=zdot[:, i].cpu().detach().numpy(),
                      mode='markers', name=f'zdot{i}',
                             marker_color='green', opacity=.5), row=2, col=1+i)



fig.update_layout(height=600, width=1200, title_text="Side By Side Subplots")
fig.show()

In [25]:
import constants as const
z_real = dataset.df.iloc[idxs][const.Z_COL_NAMES]
fig = make_subplots(rows=2, cols=3, shared_xaxes=True)

for i in range(3):
    fig.add_trace(go.Scatter(x=np.array(range(z.shape[0])),
                       y=z_real.values[:, i],
                      mode='markers', name=f'z_real{i}',
                             marker_color='blue', opacity=.5), row=1, col=1+i)
for j,i in enumerate([0, 1, 2]):
    fig.add_trace(go.Scatter(x=np.array(range(z.shape[0])),
                   y=z[:, i].cpu().detach().numpy(),
                  mode='markers', name=f'z{i}',
                         marker_color='green', opacity=.5), row=2, col=1+j,
                )


fig.update_layout(height=600, width=1200, title_text="Side By Side Subplots")
fig.show()

In [26]:
[(val, i) for val,i in enumerate(['a', 'b', 'c'])]

[(0, 'a'), (1, 'b'), (2, 'c')]

In [27]:
z_real = dataset.df.iloc[idxs][const.Z_COL_NAMES]
fig = make_subplots(rows=2, cols=3)

for real, pred in zip([0, 1, 2], [0, 2, 1]):
    fig.add_trace(go.Scatter(x=z_real.values[:, real],
                       y=z[:, pred].cpu().detach().numpy(),
                      mode='markers', name=f'z_real{i}',
                             marker_color='blue', opacity=.5), row=1, col=1+real)


fig.update_layout(height=600, width=1200, title_text="Side By Side Subplots")
fig.show()

In [ ]:
model.XI_coefficient_mask